In [1]:
import pandas as pd

# import scipy
# from scipy.stats import t
# import seaborn as sns
# from datetime import datetime, timedelta
# import plotly.express as px
# from pathlib import Path
# import statsmodels.api as sm
# from sklearn.preprocessing import StandardScaler
# from statsmodels.stats.multitest import multipletests
# from scipy.stats import f_oneway as anova
# from statsmodels.formula.api import ols 
  
# import math
# from select import select

#kernal must be restarted if these module change 
from SCP_processor import SCP_processor
processor = SCP_processor(ignore_peptides=False, ignore_proteins=False)
from SCP_plotter import SCP_plotter
plotter = SCP_plotter(write_output = True, processor=processor)

In [2]:
# Method put files in, one dictionary for each analysis, if there is only one file or you are looking in all files, 
# then you don't need @'s in your SETTINGS_FILE
WRITE_OUTPUT = True
USE_MaxLFQ = False
filelist = [
             {"input1":"input/report.pg_matrix.tsv",
             "input2":"input/report.pr_matrix.tsv",
             "input3":"input/report.pg_matrix.tsv",
             "input4":"input/report-first-pass.pr_matrix.tsv",
             "input5":"Input/Payne2/Payne_organoids2.0_InputFiles.txt",
             "process_app": "DIANN_LF"},

                      ]

            #Order of files
                #For FragPipe
                    #input1= Protein with MBR
                    #input2= Peptide with MBR
                #For DIANN
                    #input1= pg_matrix
                    #input2= pr_matrix 
                    #input3= pg_matrix MS2
                    #input4= pr_matrix MS2
                #For PD
                    #input1= Protein 
                    #input2= Peptide Groups
                    #input3= blank
                    #input4= blank
                    #input5= inpit_files


SETTINGS_FILE = "LL2076_setting.txt" #tab delimited
    #Format
    #Required Columns
        #Group Name	
        #filter_in: a string pattern contained in desired raw filenames in analysis followed by an @ + the file number (filelist index) to look in
        #filter_out: a string pattern contained in undesired raw filenames
    #Extra columns
        #can be used to group by color, layer, or x position in CV and ID graphs

In [3]:
# define group names and assign analysis to different groups(web app version was done through GUI so
# steps are taken to make sure they have same output)
x = processor.read_files(grouped_input_files=filelist)

In [4]:
data_obj = processor.outer_join_data_objects(x)

***


In [5]:
saved_settings = processor.sort_runs(data_obj, SETTINGS_FILE)

In [6]:
#ID plot(protein and peptides)
plot_options={
            "mean label": "True",
            "error bar": "ci95", #None, stdev, or ci95
            "X Title": "total",
            "Y Title": "protein Identification (MBR)",
            "color": ["#3E6990", "#7aa8e6","#AABD8C", "#E9E3B4", "#C6878F", "#fac8d3","#F39B6D",  "pink",
                  "orange", "brown", "pink", "gray", "olive", "cyan", "black","red",
                  "yellow","green","blue","indigo","violet"],
            "width": 700,
            "height": 450,
            "font": dict(size=16, family="Arial black"),
            "ID mode": "total",#grouped, total, MS2, grouped_stacked, stacked
            "Group By X": "Conditions", #ID_Mode does MS2 vs MBR
            "Group By Color": "Amount",#ID_Mode does MS2 vs MBR
            "Group By Stack": "ID_Mode",#ID_Mode does MS2 vs MBR
        }
plot_options["plot_type"] = "2" # 1 is protein, 2 is peptide
figure ,_ ,_ =plotter.ID_plots(data_obj, plot_options, saved_settings)
figure.show()

In [7]:
# CV violin plot
plot_options={    
        "median label": "True", #only works for total and MS2, can be found in CV_summary if you set WRITE_OUTPUT = True
        "box": False,
        "X Title": "Conditions (protein)",
        "Y Title": "CV of Abundance (%)",
        "color": ["#3E6990", "#7aa8e6","#C6878F", "#fac8d3","#AABD8C", "#E9E3B4",  "#F39B6D", "#C6878F", "pink",
                  "orange", "brown", "pink", "gray", "olive", "cyan", "black","red",
                  "yellow","green","blue","indigo","violet"],
        "width": 700,
        "height": 450,
        "font": dict(size=16, family="Arial black"),
        "ylimits": [-10, 400],
        "CV mode": "total",#grouped, total, MS2, grouped_stacked, stacked
        "Group By X": "Amount", #ID_Mode does MS2 vs MBR
        "Group By Color": "Organism",#ID_Mode does MS2 vs MBR
        "Group By Stack": "ID_Mode" #ID_Mode does MS2 vs MBR
    }
plot_options["plot_type"] = 2 # 1 is protein, 2 is peptide
figure, _, _ =plotter.CV_plots(data_obj, plot_options, saved_settings, missing_value_thresh=33)
figure.show()


In [8]:
# ID Venns plot
plot_options={
            "compare groups": ["Hela_SC","K562_SC"],
            "title": "Venn Diagram (protein)",
            "opacity": 0.75,
            "method": "Total",   # MS2 or Total (This determines if we only count MS2 readings or all readings)
            "color": ["#3E6990", "#C6878F", "#AABD8C","#fac8d3","#7aa8e6", "#E9E3B4","#00FF00", "#FFFF00", "#FF0000", "yellow", "red",
                      "green", "purple", "orange", "brown", "pink",
                      "gray",  "olive", "cyan", "blue",  "black", ]
        }
plot_options["plot_type"] = 2 # 1 is protein, 2 is peptide
figure, _, _ =plotter.venns_plots(data_obj, plot_options, saved_settings, username=None, miss_val_thresh=100)
figure.show()

In [9]:
# Protein Abundance Volcano plot
plot_options={
            "compare groups": ["Hela_SC","K562_SC"],
            "title": "Volcano Plot",
            "X Title": "Log2 Fold Change",
            "Y Title": "-Log10(adjusted p-value)",
            "up color": "red",
            "down color": "blue",
            "all color": "gray",
            "width": 700,
            "height": 450,
            "font": dict(size=16, family="Arial black"),
            "ylimits": [],
            "xlimits": [],
            "marker_size":8
        }
figure, _, _ =plotter.volcano_plots(data_obj, plot_options, saved_settings, missing_values_max=33)
figure.show()


In [10]:
# Protein Abundance PCA plot
plot_options={
            "compare groups": ["Hela_SC","K562_SC"],
            "title": "PCA Analysis",
            "color": ["blue", "red", "green", "black", "yellow", "purple",
                      "orange", "brown", "pink", "gray", "olive", "cyan"],
            "symbol": ['circle', 'circle', 'circle'],
            "marker_size": 8,
            "width": 700,
            "height": 450,
            "font": dict(size=16, family="Arial black"),
            "ylimits": [],
            "xlimits": []
        }
figure, _, _ =plotter.PCA_plots(data_obj, plot_options, saved_settings, missing_value_thresh=33)
figure.show()


Empty


In [11]:
# Protein Abundance Heat Map
plot_options={
            "compare groups": ["Hela_SC","K562_SC"],
            "log2_transform": False,
            "significant_only": False,
            "alpha": 0.05, 
            "min_fold_change": 2
        }
figure, _, _ =plotter.heatmap_plots(data_obj, plot_options, saved_settings, missing_value_thresh=33)
figure.show()

{'0-0': 'Hela_SC_#0', '0-1': 'Hela_SC_#1', '0-2': 'Hela_SC_#2', '0-3': 'Hela_SC_#3', '0-4': 'Hela_SC_#4', '0-5': 'Hela_SC_#5', '0-6': 'Hela_SC_#6', '0-7': 'Hela_SC_#7', '0-8': 'Hela_SC_#8', '0-9': 'Hela_SC_#9', '0-10': 'Hela_SC_#10', '0-11': 'Hela_SC_#11', '0-12': 'Hela_SC_#12', '0-13': 'Hela_SC_#13', '0-14': 'Hela_SC_#14', '0-15': 'Hela_SC_#15', '0-16': 'Hela_SC_#16', '0-17': 'Hela_SC_#17', '0-18': 'Hela_SC_#18', '0-19': 'Hela_SC_#19'}
Empty
{'0-20': 'K562_SC_#0', '0-21': 'K562_SC_#1', '0-22': 'K562_SC_#2', '0-23': 'K562_SC_#3', '0-24': 'K562_SC_#4', '0-25': 'K562_SC_#5', '0-26': 'K562_SC_#6', '0-27': 'K562_SC_#7', '0-28': 'K562_SC_#8', '0-29': 'K562_SC_#9', '0-30': 'K562_SC_#10', '0-31': 'K562_SC_#11', '0-32': 'K562_SC_#12', '0-33': 'K562_SC_#13', '0-34': 'K562_SC_#14', '0-35': 'K562_SC_#15', '0-36': 'K562_SC_#16', '0-37': 'K562_SC_#17', '0-38': 'K562_SC_#18', '0-39': 'K562_SC_#19'}
******************************************************************************************************